In [1]:
# Third-party packages
import matplotlib.pyplot as plt
import numpy as np
import pandas as pd
from pandas import datetime
from scipy.spatial.distance import cdist

import time
from scipy.interpolate import interp1d
from scipy.spatial import cKDTree
from tqdm.notebook import trange, tqdm
import seaborn as sns 
import geopandas as gpd
from shapely.geometry import Point, Polygon
from math import sqrt,atan,pi
import pyproj

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/4293023051.py:5: FutureWarning: The pandas.datetime class is deprecated and will be removed from pandas in a future version. Import from datetime module instead.
  from pandas import datetime


In [2]:
path = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/nati_v1_gen_build_cost_wave_offshore_wind.csv'
wave_costs = pd.read_csv(path, index_col='index')
wave_costs

generation_project  build_year  gen_fixed_om  gen_overnight_cost
index                                                                  
0              1300000000        2015      450600.0          8784000.00
0              1300000000        2016      427200.0          8328000.00
0              1300000000        2017      403800.0          7872000.00
0              1300000000        2018      380400.0          7416000.00
0              1300000000        2019      357000.0          6960000.00
...                   ...         ...           ...                 ...
199            1300000199        2046      112297.5          2271759.00
199            1300000199        2047      112297.5          2249041.20
199            1300000199        2048      112297.5          2226550.20
199            1300000199        2049      112297.5          2204284.95
199            1300000199        2050      112297.5          2182242.30

[7700 rows x 4 columns]

In [3]:
for id in range(0,200):
    new = pd.DataFrame(list(range(2010,2061)))
    new['index'] = id
    new['generation_project'] = (id+1300000000)
    if (id == 0):
        new_costs = new
    else:
        new_costs = pd.concat([new_costs, new])
new_costs.rename(columns={0:'build_year'},inplace=True)
new_costs = new_costs[['index','generation_project','build_year']]
new_costs

index  generation_project  build_year
0       0          1300000000        2010
1       0          1300000000        2011
2       0          1300000000        2012
3       0          1300000000        2013
4       0          1300000000        2014
..    ...                 ...         ...
46    199          1300000199        2056
47    199          1300000199        2057
48    199          1300000199        2058
49    199          1300000199        2059
50    199          1300000199        2060

[10200 rows x 3 columns]

In [4]:
len(list(range(2010,2061)))

51

In [5]:
path = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/offshore_wind_cost_proj_nrel.csv'
wind_costs = pd.read_csv(path)
wind_costs

year  CAPEX ($2020/MW)  CAPEX ($2018/MW)  Fixed O&M ($2020/MW-yr)  \
0   2010           3628193       3521886.945                   111496   
1   2011           3628193       3521886.945                   111496   
2   2012           3628193       3521886.945                   111496   
3   2013           3628193       3521886.945                   111496   
4   2014           3628193       3521886.945                   111496   
5   2015           3628193       3521886.945                   111496   
6   2016           3628193       3521886.945                   111496   
7   2017           3628193       3521886.945                   111496   
8   2018           3628193       3521886.945                   111496   
9   2019           3628193       3521886.945                   111496   
10  2020           3628193       3521886.945                   111496   
11  2021           3304479       3207657.765                   106555   
12  2022           3148688       3056431.442                   102722   
13  2023           3038152       2949134.146                    99590   
14  2024           2952414       2865908.270                    96942   
15  2025           2882361       2797907.823                    94648   
16  2026           2823132       2740414.232                    92625   
17  2027           2771826       2690611.498                    90815   
18  2028           2726570       2646681.499                    89178   
19  2029           2686088       2607385.622                    87684   
20  2030           2649467       2571837.617                    86309   
21  2031           2616035       2539385.175                    85036   
22  2032           2585280       2509531.296                    83851   
23  2033           2556806       2481891.584                    82742   
24  2034           2530297       2456159.298                    81701   
25  2035           2505500       2432088.850                    80719   
26  2036           2482206       2409477.364                    79790   
27  2037           2460244       2388158.851                    78909   
28  2038           2439470       2367993.529                    78071   
29  2039           2419762       2348862.973                    77272   
30  2040           2401015       2330665.261                    76508   
31  2041           2383141       2313314.969                    75777   
32  2042           2366061       2296735.413                    75076   
33  2043           2349709       2280862.526                    74402   
34  2044           2334024       2265637.097                    73754   
35  2045           2318954       2251008.648                    73129   
36  2046           2304453       2236932.527                    72527   
37  2047           2290480       2223368.936                    71944   
38  2048           2276996       2210280.017                    71381   
39  2049           2263971       2197636.650                    70836   
40  2050           2251372       2185406.800                    70307   

    Fixed O&M ($2018/MW-yr)  
0               108229.1672  
1               108229.1672  
2               108229.1672  
3               108229.1672  
4               108229.1672  
5               108229.1672  
6               108229.1672  
7               108229.1672  
8               108229.1672  
9               108229.1672  
10              108229.1672  
11              103432.9385  
12               99712.2454  
13               96672.0130  
14               94101.5994  
15               91874.8136  
16               89911.0875  
17               88154.1205  
18               86565.0846  
19               85114.8588  
20               83780.1463  
21               82544.4452  
22               81394.1657  
23               80317.6594  
24               79307.1607  
25               78353.9333  
26               77452.1530  
27               76596.9663  
28               75783.5197  
29               75007.9304  
30     

In [6]:
wind_costs_ext = wind_costs.copy()
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[41], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[41] = 2051
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[42], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[42] = 2052
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[43], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[43] = 2053
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[44], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[44] = 2054
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[45], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[45] = 2055
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[46], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[46] = 2056
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[47], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[47] = 2057
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[48], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[48] = 2058
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[49], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[49] = 2059
new_row = pd.DataFrame(wind_costs_ext[-1:].values, index=[50], columns=wind_costs_ext.columns)
wind_costs_ext = wind_costs_ext.append(new_row)
wind_costs_ext['year'].loc[50] = 2060
wind_costs_ext

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1992280636.py:3: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  wind_costs_ext = wind_costs_ext.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1992280636.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  wind_costs_ext = wind_costs_ext.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1992280636.py:9: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  wind_costs_ext = wind_costs_ext.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1992280636.py:12: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.conca

year  CAPEX ($2020/MW)  CAPEX ($2018/MW)  Fixed O&M ($2020/MW-yr)  \
0   2010.0         3628193.0       3521886.945                 111496.0   
1   2011.0         3628193.0       3521886.945                 111496.0   
2   2012.0         3628193.0       3521886.945                 111496.0   
3   2013.0         3628193.0       3521886.945                 111496.0   
4   2014.0         3628193.0       3521886.945                 111496.0   
5   2015.0         3628193.0       3521886.945                 111496.0   
6   2016.0         3628193.0       3521886.945                 111496.0   
7   2017.0         3628193.0       3521886.945                 111496.0   
8   2018.0         3628193.0       3521886.945                 111496.0   
9   2019.0         3628193.0       3521886.945                 111496.0   
10  2020.0         3628193.0       3521886.945                 111496.0   
11  2021.0         3304479.0       3207657.765                 106555.0   
12  2022.0         3148688.0       3056431.442                 102722.0   
13  2023.0         3038152.0       2949134.146                  99590.0   
14  2024.0         2952414.0       2865908.270                  96942.0   
15  2025.0         2882361.0       2797907.823                  94648.0   
16  2026.0         2823132.0       2740414.232                  92625.0   
17  2027.0         2771826.0       2690611.498                  90815.0   
18  2028.0         2726570.0       2646681.499                  89178.0   
19  2029.0         2686088.0       2607385.622                  87684.0   
20  2030.0         2649467.0       2571837.617                  86309.0   
21  2031.0         2616035.0       2539385.175                  85036.0   
22  2032.0         2585280.0       2509531.296                  83851.0   
23  2033.0         2556806.0       2481891.584                  82742.0   
24  2034.0         2530297.0       2456159.298                  81701.0   
25  2035.0         2505500.0       2432088.850                  80719.0   
26  2036.0         2482206.0       2409477.364                  79790.0   
27  2037.0         2460244.0       2388158.851                  78909.0   
28  2038.0         2439470.0       2367993.529                  78071.0   
29  2039.0         2419762.0       2348862.973                  77272.0   
30  2040.0         2401015.0       2330665.261                  76508.0   
31  2041.0         2383141.0       2313314.969                  75777.0   
32  2042.0         2366061.0       2296735.413                  75076.0   
33  2043.0         2349709.0       2280862.526                  74402.0   
34  2044.0         2334024.0       2265637.097                  73754.0   
35  2045.0         2318954.0       2251008.648                  73129.0   
36  2046.0         2304453.0       2236932.527                  72527.0   
37  2047.0         2290480.0       2223368.936                  71944.0   
38  2048.0         2276996.0       2210280.017                  71381.0   
39  2049.0         2263971.0       2197636.650                  70836.0   
40  2050.0         2251372.0       2185406.800                  70307.0   
41  2051.0         2251372.0       2185406.800                  70307.0   
42  2052.0         2251372.0       2185406.800                  70307.0   
43  2053.0         2251372.0       2185406.800                  70307.0   
44  2054.0         2251372.0       2185406.800                  70307.0   
45  2055.0         2251372.0       2185406.800                  70307.0   
46  2056.0         2251372.0       2185406.800                  70307.0   
47  2057.0         2251372.0       2185406.800                  70307.0   
48  2058.0         2251372.0       2185406.800                  70307.0   
49  2059.0         2251372.0       2185406.800                  70307.0   
50  2060.0         2251372.0       2185406.800                  70307.0   

    Fixed O&M ($2018/MW-yr)  
0               108229.1672  
1               108229.1672  
2              

In [7]:
costs0 = new_costs[new_costs['index'] == 0]
costs0.shape

(51, 3)

In [11]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 1462000 #scenario 1
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind = wind_costs_ext['CAPEX ($2018/MW)']
    oc_wind = pd.DataFrame(oc_wind)
    oc_wind['index'] = d
    oc_wind['build_year'] = years_w['build_year']
    oc_wind.rename(columns={'CAPEX ($2018/MW)':'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind])

oc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/4172995959.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/4172995959.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/4172995959.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/4172995959.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_

index  gen_overnight_cost  build_year
0     0.0            346500.0      2010.0
1     0.0            374387.5      2011.0
2     0.0            402275.0      2012.0
3     0.0            430162.5      2013.0
4     0.0            458050.0      2014.0
..    ...                 ...         ...
46  199.0           2185406.8      2056.0
47  199.0           2185406.8      2057.0
48  199.0           2185406.8      2058.0
49  199.0           2185406.8      2059.0
50  199.0           2185406.8      2060.0

[10200 rows x 3 columns]

In [13]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 43000 #scenario 1
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind = wind_costs_ext['Fixed O&M ($2018/MW-yr)']
    omc_wind = pd.DataFrame(omc_wind)
    omc_wind['index'] = d
    omc_wind['build_year'] = years_w['build_year']
    omc_wind.rename(columns={'Fixed O&M ($2018/MW-yr)':'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3568448204.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3568448204.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3568448204.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3568448204.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  om

index  gen_fixed_om  build_year
0     0.0    10540.0000      2010.0
1     0.0    11351.5000      2011.0
2     0.0    12163.0000      2012.0
3     0.0    12974.5000      2013.0
4     0.0    13786.0000      2014.0
..    ...           ...         ...
46  199.0    68247.0049      2056.0
47  199.0    68247.0049      2057.0
48  199.0    68247.0049      2058.0
49  199.0    68247.0049      2059.0
50  199.0    68247.0049      2060.0

[10200 rows x 3 columns]

In [16]:
scenario_1 = new_costs.copy()
scenario_1['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_1['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_1 = scenario_1[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_1

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010    10540.0000            346500.0
1       0          1300000000        2011    11351.5000            374387.5
2       0          1300000000        2012    12163.0000            402275.0
3       0          1300000000        2013    12974.5000            430162.5
4       0          1300000000        2014    13786.0000            458050.0
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056    68247.0049           2185406.8
47    199          1300000199        2057    68247.0049           2185406.8
48    199          1300000199        2058    68247.0049           2185406.8
49    199          1300000199        2059    68247.0049           2185406.8
50    199          1300000199        2060    68247.0049           2185406.8

[10200 rows x 5 columns]

In [17]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_1_gen_build_cost_wave_offshore_wind.csv'
scenario_1.to_csv(output_path,index=False)

In [18]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 1333324 #scenario 2
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind = wind_costs_ext['CAPEX ($2018/MW)']
    oc_wind = pd.DataFrame(oc_wind)
    oc_wind['index'] = d
    oc_wind['build_year'] = years_w['build_year']
    oc_wind.rename(columns={'CAPEX ($2018/MW)':'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind])

oc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1199051630.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1199051630.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1199051630.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1199051630.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_

index  gen_overnight_cost  build_year
0     0.0            346500.0      2010.0
1     0.0            371170.6      2011.0
2     0.0            395841.2      2012.0
3     0.0            420511.8      2013.0
4     0.0            445182.4      2014.0
..    ...                 ...         ...
46  199.0           2185406.8      2056.0
47  199.0           2185406.8      2057.0
48  199.0           2185406.8      2058.0
49  199.0           2185406.8      2059.0
50  199.0           2185406.8      2060.0

[10200 rows x 3 columns]

In [19]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 22624 #scenario 2
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind = wind_costs_ext['Fixed O&M ($2018/MW-yr)']
    omc_wind = pd.DataFrame(omc_wind)
    omc_wind['index'] = d
    omc_wind['build_year'] = years_w['build_year']
    omc_wind.rename(columns={'Fixed O&M ($2018/MW-yr)':'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/256130309.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/256130309.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/256130309.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/256130309.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wa

index  gen_fixed_om  build_year
0     0.0    10540.0000      2010.0
1     0.0    10842.1000      2011.0
2     0.0    11144.2000      2012.0
3     0.0    11446.3000      2013.0
4     0.0    11748.4000      2014.0
..    ...           ...         ...
46  199.0    68247.0049      2056.0
47  199.0    68247.0049      2057.0
48  199.0    68247.0049      2058.0
49  199.0    68247.0049      2059.0
50  199.0    68247.0049      2060.0

[10200 rows x 3 columns]

In [20]:
scenario_2 = new_costs.copy()
scenario_2['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_2['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_2 = scenario_2[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_2

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010    10540.0000            346500.0
1       0          1300000000        2011    10842.1000            371170.6
2       0          1300000000        2012    11144.2000            395841.2
3       0          1300000000        2013    11446.3000            420511.8
4       0          1300000000        2014    11748.4000            445182.4
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056    68247.0049           2185406.8
47    199          1300000199        2057    68247.0049           2185406.8
48    199          1300000199        2058    68247.0049           2185406.8
49    199          1300000199        2059    68247.0049           2185406.8
50    199          1300000199        2060    68247.0049           2185406.8

[10200 rows x 5 columns]

In [25]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_2_gen_build_cost_wave_offshore_wind.csv'
scenario_2.to_csv(output_path,index=False)

In [22]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 760000 #scenario 3
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind = wind_costs_ext['CAPEX ($2018/MW)']
    oc_wind = pd.DataFrame(oc_wind)
    oc_wind['index'] = d
    oc_wind['build_year'] = years_w['build_year']
    oc_wind.rename(columns={'CAPEX ($2018/MW)':'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind])

oc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3214331118.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3214331118.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3214331118.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3214331118.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_

index  gen_overnight_cost  build_year
0     0.0            346500.0      2010.0
1     0.0            356837.5      2011.0
2     0.0            367175.0      2012.0
3     0.0            377512.5      2013.0
4     0.0            387850.0      2014.0
..    ...                 ...         ...
46  199.0           2185406.8      2056.0
47  199.0           2185406.8      2057.0
48  199.0           2185406.8      2058.0
49  199.0           2185406.8      2059.0
50  199.0           2185406.8      2060.0

[10200 rows x 3 columns]

In [23]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 33108 #scenario 3
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind = wind_costs_ext['Fixed O&M ($2018/MW-yr)']
    omc_wind = pd.DataFrame(omc_wind)
    omc_wind['index'] = d
    omc_wind['build_year'] = years_w['build_year']
    omc_wind.rename(columns={'Fixed O&M ($2018/MW-yr)':'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2631953353.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2631953353.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2631953353.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2631953353.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  om

index  gen_fixed_om  build_year
0     0.0    10540.0000      2010.0
1     0.0    11104.2000      2011.0
2     0.0    11668.4000      2012.0
3     0.0    12232.6000      2013.0
4     0.0    12796.8000      2014.0
..    ...           ...         ...
46  199.0    68247.0049      2056.0
47  199.0    68247.0049      2057.0
48  199.0    68247.0049      2058.0
49  199.0    68247.0049      2059.0
50  199.0    68247.0049      2060.0

[10200 rows x 3 columns]

In [24]:
scenario_3 = new_costs.copy()
scenario_3['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_3['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_3 = scenario_3[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_3

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010    10540.0000            346500.0
1       0          1300000000        2011    11104.2000            356837.5
2       0          1300000000        2012    11668.4000            367175.0
3       0          1300000000        2013    12232.6000            377512.5
4       0          1300000000        2014    12796.8000            387850.0
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056    68247.0049           2185406.8
47    199          1300000199        2057    68247.0049           2185406.8
48    199          1300000199        2058    68247.0049           2185406.8
49    199          1300000199        2059    68247.0049           2185406.8
50    199          1300000199        2060    68247.0049           2185406.8

[10200 rows x 5 columns]

In [26]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_3_gen_build_cost_wave_offshore_wind.csv'
scenario_3.to_csv(output_path,index=False)

In [27]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 617612 #scenario 4
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind = wind_costs_ext['CAPEX ($2018/MW)']
    oc_wind = pd.DataFrame(oc_wind)
    oc_wind['index'] = d
    oc_wind['build_year'] = years_w['build_year']
    oc_wind.rename(columns={'CAPEX ($2018/MW)':'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind])

oc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/676873271.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/676873271.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/676873271.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/676873271.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df =

index  gen_overnight_cost  build_year
0     0.0            346500.0      2010.0
1     0.0            353277.8      2011.0
2     0.0            360055.6      2012.0
3     0.0            366833.4      2013.0
4     0.0            373611.2      2014.0
..    ...                 ...         ...
46  199.0           2185406.8      2056.0
47  199.0           2185406.8      2057.0
48  199.0           2185406.8      2058.0
49  199.0           2185406.8      2059.0
50  199.0           2185406.8      2060.0

[10200 rows x 3 columns]

In [28]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 13252 #scenario 4
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind = wind_costs_ext['Fixed O&M ($2018/MW-yr)']
    omc_wind = pd.DataFrame(omc_wind)
    omc_wind['index'] = d
    omc_wind['build_year'] = years_w['build_year']
    omc_wind.rename(columns={'Fixed O&M ($2018/MW-yr)':'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1132657252.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1132657252.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1132657252.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1132657252.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  om

index  gen_fixed_om  build_year
0     0.0    10540.0000      2010.0
1     0.0    10607.8000      2011.0
2     0.0    10675.6000      2012.0
3     0.0    10743.4000      2013.0
4     0.0    10811.2000      2014.0
..    ...           ...         ...
46  199.0    68247.0049      2056.0
47  199.0    68247.0049      2057.0
48  199.0    68247.0049      2058.0
49  199.0    68247.0049      2059.0
50  199.0    68247.0049      2060.0

[10200 rows x 3 columns]

In [29]:
scenario_4 = new_costs.copy()
scenario_4['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_4['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_4 = scenario_4[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_4

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010    10540.0000            346500.0
1       0          1300000000        2011    10607.8000            353277.8
2       0          1300000000        2012    10675.6000            360055.6
3       0          1300000000        2013    10743.4000            366833.4
4       0          1300000000        2014    10811.2000            373611.2
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056    68247.0049           2185406.8
47    199          1300000199        2057    68247.0049           2185406.8
48    199          1300000199        2058    68247.0049           2185406.8
49    199          1300000199        2059    68247.0049           2185406.8
50    199          1300000199        2060    68247.0049           2185406.8

[10200 rows x 5 columns]

In [30]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_4_gen_build_cost_wave_offshore_wind.csv'
scenario_4.to_csv(output_path,index=False)

In [31]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 400000 #scenario 5
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind = wind_costs_ext['CAPEX ($2018/MW)']
    oc_wind = pd.DataFrame(oc_wind)
    oc_wind['index'] = d
    oc_wind['build_year'] = years_w['build_year']
    oc_wind.rename(columns={'CAPEX ($2018/MW)':'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind])

oc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2080039338.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2080039338.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2080039338.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2080039338.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_

index  gen_overnight_cost  build_year
0     0.0            346500.0      2010.0
1     0.0            347837.5      2011.0
2     0.0            349175.0      2012.0
3     0.0            350512.5      2013.0
4     0.0            351850.0      2014.0
..    ...                 ...         ...
46  199.0           2185406.8      2056.0
47  199.0           2185406.8      2057.0
48  199.0           2185406.8      2058.0
49  199.0           2185406.8      2059.0
50  199.0           2185406.8      2060.0

[10200 rows x 3 columns]

In [32]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 8000 #scenario 5
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind = wind_costs_ext['Fixed O&M ($2018/MW-yr)']
    omc_wind = pd.DataFrame(omc_wind)
    omc_wind['index'] = d
    omc_wind['build_year'] = years_w['build_year']
    omc_wind.rename(columns={'Fixed O&M ($2018/MW-yr)':'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1482508447.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1482508447.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1482508447.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1482508447.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  om

index  gen_fixed_om  build_year
0     0.0    10540.0000      2010.0
1     0.0    10476.5000      2011.0
2     0.0    10413.0000      2012.0
3     0.0    10349.5000      2013.0
4     0.0    10286.0000      2014.0
..    ...           ...         ...
46  199.0    68247.0049      2056.0
47  199.0    68247.0049      2057.0
48  199.0    68247.0049      2058.0
49  199.0    68247.0049      2059.0
50  199.0    68247.0049      2060.0

[10200 rows x 3 columns]

In [34]:
scenario_5 = new_costs.copy()
scenario_5['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_5['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_5 = scenario_5[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_5

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010    10540.0000            346500.0
1       0          1300000000        2011    10476.5000            347837.5
2       0          1300000000        2012    10413.0000            349175.0
3       0          1300000000        2013    10349.5000            350512.5
4       0          1300000000        2014    10286.0000            351850.0
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056    68247.0049           2185406.8
47    199          1300000199        2057    68247.0049           2185406.8
48    199          1300000199        2058    68247.0049           2185406.8
49    199          1300000199        2059    68247.0049           2185406.8
50    199          1300000199        2060    68247.0049           2185406.8

[10200 rows x 5 columns]

In [35]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_5_gen_build_cost_wave_offshore_wind.csv'
scenario_5.to_csv(output_path,index=False)

In [54]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 1462000 #scenario 6
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    wind_high = 3628193 #do not change
    wind_low = 2251372 #scenario 6
    oc_wind = list(np.linspace(wind_high,wind_low,51))
    oc_wind_df = pd.DataFrame(oc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind_df['index'] = d
    oc_wind_df['build_year'] = years_w['build_year']
    oc_wind_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind_df])

oc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1566679884.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1566679884.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1566679884.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1566679884.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_

index  gen_overnight_cost  build_year
0     0.0           346500.00      2010.0
1     0.0           374387.50      2011.0
2     0.0           402275.00      2012.0
3     0.0           430162.50      2013.0
4     0.0           458050.00      2014.0
..    ...                 ...         ...
46  199.0          2361517.68      2056.0
47  199.0          2333981.26      2057.0
48  199.0          2306444.84      2058.0
49  199.0          2278908.42      2059.0
50  199.0          2251372.00      2060.0

[10200 rows x 3 columns]

In [55]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 43000 #scenario 6
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    wind_high = 111496 #do not change
    wind_low = 70307 #scenario 6
    omc_wind = list(np.linspace(wind_high,wind_low,51))
    omc_wind_df = pd.DataFrame(omc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind_df['index'] = d
    omc_wind_df['build_year'] = years_w['build_year']
    omc_wind_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind_df])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2430536790.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2430536790.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2430536790.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2430536790.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  om

index  gen_fixed_om  build_year
0     0.0      10540.00      2010.0
1     0.0      11351.50      2011.0
2     0.0      12163.00      2012.0
3     0.0      12974.50      2013.0
4     0.0      13786.00      2014.0
..    ...           ...         ...
46  199.0      73602.12      2056.0
47  199.0      72778.34      2057.0
48  199.0      71954.56      2058.0
49  199.0      71130.78      2059.0
50  199.0      70307.00      2060.0

[10200 rows x 3 columns]

In [56]:
scenario_6 = new_costs.copy()
scenario_6['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_6['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_6 = scenario_6[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_6

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010      10540.00           346500.00
1       0          1300000000        2011      11351.50           374387.50
2       0          1300000000        2012      12163.00           402275.00
3       0          1300000000        2013      12974.50           430162.50
4       0          1300000000        2014      13786.00           458050.00
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056      73602.12          2361517.68
47    199          1300000199        2057      72778.34          2333981.26
48    199          1300000199        2058      71954.56          2306444.84
49    199          1300000199        2059      71130.78          2278908.42
50    199          1300000199        2060      70307.00          2251372.00

[10200 rows x 5 columns]

In [57]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_6_gen_build_cost_wave_offshore_wind.csv'
scenario_6.to_csv(output_path,index=False)

In [59]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 1333324 #scenario 7
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    wind_high = 3628193 #do not change
    wind_low = 2054029 #scenario 7
    oc_wind = list(np.linspace(wind_high,wind_low,51))
    oc_wind_df = pd.DataFrame(oc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind_df['index'] = d
    oc_wind_df['build_year'] = years_w['build_year']
    oc_wind_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind_df])

oc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2810440990.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2810440990.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2810440990.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2810440990.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_

index  gen_overnight_cost  build_year
0     0.0           346500.00      2010.0
1     0.0           371170.60      2011.0
2     0.0           395841.20      2012.0
3     0.0           420511.80      2013.0
4     0.0           445182.40      2014.0
..    ...                 ...         ...
46  199.0          2179962.12      2056.0
47  199.0          2148478.84      2057.0
48  199.0          2116995.56      2058.0
49  199.0          2085512.28      2059.0
50  199.0          2054029.00      2060.0

[10200 rows x 3 columns]

In [60]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 22624 #scenario 7
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    wind_high = 111496 #do not change
    wind_low = 63480 #scenario 7
    omc_wind = list(np.linspace(wind_high,wind_low,51))
    omc_wind_df = pd.DataFrame(omc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind_df['index'] = d
    omc_wind_df['build_year'] = years_w['build_year']
    omc_wind_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind_df])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1845838395.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1845838395.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1845838395.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/1845838395.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  om

index  gen_fixed_om  build_year
0     0.0      10540.00      2010.0
1     0.0      10842.10      2011.0
2     0.0      11144.20      2012.0
3     0.0      11446.30      2013.0
4     0.0      11748.40      2014.0
..    ...           ...         ...
46  199.0      67321.28      2056.0
47  199.0      66360.96      2057.0
48  199.0      65400.64      2058.0
49  199.0      64440.32      2059.0
50  199.0      63480.00      2060.0

[10200 rows x 3 columns]

In [61]:
scenario_7 = new_costs.copy()
scenario_7['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_7['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_7 = scenario_7[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_7

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010      10540.00           346500.00
1       0          1300000000        2011      10842.10           371170.60
2       0          1300000000        2012      11144.20           395841.20
3       0          1300000000        2013      11446.30           420511.80
4       0          1300000000        2014      11748.40           445182.40
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056      67321.28          2179962.12
47    199          1300000199        2057      66360.96          2148478.84
48    199          1300000199        2058      65400.64          2116995.56
49    199          1300000199        2059      64440.32          2085512.28
50    199          1300000199        2060      63480.00          2054029.00

[10200 rows x 5 columns]

In [62]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_7_gen_build_cost_wave_offshore_wind.csv'
scenario_7.to_csv(output_path,index=False)

In [63]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 760000 #scenario 8
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    wind_high = 3628193 #do not change
    wind_low = 1856686 #scenario 8
    oc_wind = list(np.linspace(wind_high,wind_low,51))
    oc_wind_df = pd.DataFrame(oc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind_df['index'] = d
    oc_wind_df['build_year'] = years_w['build_year']
    oc_wind_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind_df])

oc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3647960158.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3647960158.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3647960158.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3647960158.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_

index  gen_overnight_cost  build_year
0     0.0           346500.00      2010.0
1     0.0           356837.50      2011.0
2     0.0           367175.00      2012.0
3     0.0           377512.50      2013.0
4     0.0           387850.00      2014.0
..    ...                 ...         ...
46  199.0          1998406.56      2056.0
47  199.0          1962976.42      2057.0
48  199.0          1927546.28      2058.0
49  199.0          1892116.14      2059.0
50  199.0          1856686.00      2060.0

[10200 rows x 3 columns]

In [64]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 33108 #scenario 8
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    wind_high = 111496 #do not change
    wind_low = 56653 #scenario 8
    omc_wind = list(np.linspace(wind_high,wind_low,51))
    omc_wind_df = pd.DataFrame(omc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind_df['index'] = d
    omc_wind_df['build_year'] = years_w['build_year']
    omc_wind_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind_df])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3257389082.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3257389082.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3257389082.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3257389082.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  om

index  gen_fixed_om  build_year
0     0.0      10540.00      2010.0
1     0.0      11104.20      2011.0
2     0.0      11668.40      2012.0
3     0.0      12232.60      2013.0
4     0.0      12796.80      2014.0
..    ...           ...         ...
46  199.0      61040.44      2056.0
47  199.0      59943.58      2057.0
48  199.0      58846.72      2058.0
49  199.0      57749.86      2059.0
50  199.0      56653.00      2060.0

[10200 rows x 3 columns]

In [65]:
scenario_8 = new_costs.copy()
scenario_8['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_8['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_8 = scenario_8[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_8

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010      10540.00           346500.00
1       0          1300000000        2011      11104.20           356837.50
2       0          1300000000        2012      11668.40           367175.00
3       0          1300000000        2013      12232.60           377512.50
4       0          1300000000        2014      12796.80           387850.00
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056      61040.44          1998406.56
47    199          1300000199        2057      59943.58          1962976.42
48    199          1300000199        2058      58846.72          1927546.28
49    199          1300000199        2059      57749.86          1892116.14
50    199          1300000199        2060      56653.00          1856686.00

[10200 rows x 5 columns]

In [66]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_8_gen_build_cost_wave_offshore_wind.csv'
scenario_8.to_csv(output_path,index=False)

In [67]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 617612 #scenario 9
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    wind_high = 3628193 #do not change
    wind_low = 1659343 #scenario 9
    oc_wind = list(np.linspace(wind_high,wind_low,51))
    oc_wind_df = pd.DataFrame(oc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind_df['index'] = d
    oc_wind_df['build_year'] = years_w['build_year']
    oc_wind_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind_df])

oc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2145893734.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2145893734.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2145893734.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2145893734.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_

index  gen_overnight_cost  build_year
0     0.0            346500.0      2010.0
1     0.0            353277.8      2011.0
2     0.0            360055.6      2012.0
3     0.0            366833.4      2013.0
4     0.0            373611.2      2014.0
..    ...                 ...         ...
46  199.0           1816851.0      2056.0
47  199.0           1777474.0      2057.0
48  199.0           1738097.0      2058.0
49  199.0           1698720.0      2059.0
50  199.0           1659343.0      2060.0

[10200 rows x 3 columns]

In [68]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 13252 #scenario 9
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    wind_high = 111496 #do not change
    wind_low = 49826 #scenario 9
    omc_wind = list(np.linspace(wind_high,wind_low,51))
    omc_wind_df = pd.DataFrame(omc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind_df['index'] = d
    omc_wind_df['build_year'] = years_w['build_year']
    omc_wind_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind_df])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3303354555.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3303354555.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3303354555.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3303354555.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  om

index  gen_fixed_om  build_year
0     0.0       10540.0      2010.0
1     0.0       10607.8      2011.0
2     0.0       10675.6      2012.0
3     0.0       10743.4      2013.0
4     0.0       10811.2      2014.0
..    ...           ...         ...
46  199.0       54759.6      2056.0
47  199.0       53526.2      2057.0
48  199.0       52292.8      2058.0
49  199.0       51059.4      2059.0
50  199.0       49826.0      2060.0

[10200 rows x 3 columns]

In [69]:
scenario_9 = new_costs.copy()
scenario_9['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_9['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_9 = scenario_9[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_9

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010       10540.0            346500.0
1       0          1300000000        2011       10607.8            353277.8
2       0          1300000000        2012       10675.6            360055.6
3       0          1300000000        2013       10743.4            366833.4
4       0          1300000000        2014       10811.2            373611.2
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056       54759.6           1816851.0
47    199          1300000199        2057       53526.2           1777474.0
48    199          1300000199        2058       52292.8           1738097.0
49    199          1300000199        2059       51059.4           1698720.0
50    199          1300000199        2060       49826.0           1659343.0

[10200 rows x 5 columns]

In [70]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_9_gen_build_cost_wave_offshore_wind.csv'
scenario_9.to_csv(output_path,index=False)

In [71]:
#Overnight costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_oc_high = 346500 #do not change
    wave_oc_low = 400000 #scenario 10
    oc_wave = list(np.linspace(wave_oc_high,wave_oc_low,41))
    oc_wave_df = pd.DataFrame(oc_wave).reset_index()
    oc_wave_df['index'] = c
    oc_wave_df['build_year'] = years['build_year']
    oc_wave_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_wave_df.loc[36,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[37,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[38,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    oc_wave_df.loc[39,'gen_overnight_cost'] = oc_wave_df.iloc[40]['gen_overnight_cost']
    for ix in range(41,51):
        new_row = pd.DataFrame(oc_wave_df.iloc[[40]].values, index=[ix], columns=oc_wave_df.columns)
        oc_wave_df = oc_wave_df.append(new_row)
        oc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        oc_cost = oc_wave_df
    else:
        oc_cost = pd.concat([oc_cost, oc_wave_df])

for d in range(100,200):
    wind_high = 3628193 #do not change
    wind_low = 1462000 #scenario 10
    oc_wind = list(np.linspace(wind_high,wind_low,51))
    oc_wind_df = pd.DataFrame(oc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    oc_wind_df['index'] = d
    oc_wind_df['build_year'] = years_w['build_year']
    oc_wind_df.rename(columns={0:'gen_overnight_cost'}, inplace=True)
    oc_cost = pd.concat([oc_cost, oc_wind_df])

oc_cost


/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2595162591.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2595162591.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2595162591.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_df = oc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/2595162591.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  oc_wave_

index  gen_overnight_cost  build_year
0     0.0           346500.00      2010.0
1     0.0           347837.50      2011.0
2     0.0           349175.00      2012.0
3     0.0           350512.50      2013.0
4     0.0           351850.00      2014.0
..    ...                 ...         ...
46  199.0          1635295.44      2056.0
47  199.0          1591971.58      2057.0
48  199.0          1548647.72      2058.0
49  199.0          1505323.86      2059.0
50  199.0          1462000.00      2060.0

[10200 rows x 3 columns]

In [72]:
#Fixed O&M costs
for c in range(0,100):
    years = pd.DataFrame(list(range(2010,2051)))
    years.rename(columns={0:'build_year'},inplace=True)
    wave_omc_high = 10540 #do not change
    wave_omc_low = 8000 #scenario 10
    omc_wave = list(np.linspace(wave_omc_high,wave_omc_low,41))
    omc_wave_df = pd.DataFrame(omc_wave).reset_index()
    omc_wave_df['index'] = c
    omc_wave_df['build_year'] = years['build_year']
    omc_wave_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_wave_df.loc[36,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[37,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[38,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    omc_wave_df.loc[39,'gen_fixed_om'] = omc_wave_df.iloc[40]['gen_fixed_om']
    for ix in range(41,51):
        new_row = pd.DataFrame(omc_wave_df.iloc[[40]].values, index=[ix], columns=omc_wave_df.columns)
        omc_wave_df = omc_wave_df.append(new_row)
        omc_wave_df.loc[ix,'build_year'] = (ix+2010)

    if (c == 0):
        omc_cost = omc_wave_df
    else:
        omc_cost = pd.concat([omc_cost, omc_wave_df])

for d in range(100,200):
    wind_high = 111496 #do not change
    wind_low = 43000 #scenario 10
    omc_wind = list(np.linspace(wind_high,wind_low,51))
    omc_wind_df = pd.DataFrame(omc_wind).reset_index()
    years_w = pd.DataFrame(list(range(2010,2061)))
    years_w.rename(columns={0:'build_year'},inplace=True)
    omc_wind_df['index'] = d
    omc_wind_df['build_year'] = years_w['build_year']
    omc_wind_df.rename(columns={0:'gen_fixed_om'}, inplace=True)
    omc_cost = pd.concat([omc_cost, omc_wind_df])

omc_cost

/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3001561283.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3001561283.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3001561283.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  omc_wave_df = omc_wave_df.append(new_row)
/var/folders/bd/5zkgv6rx32s3b0jx_9373xhc0000gn/T/ipykernel_19732/3001561283.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  om

index  gen_fixed_om  build_year
0     0.0      10540.00      2010.0
1     0.0      10476.50      2011.0
2     0.0      10413.00      2012.0
3     0.0      10349.50      2013.0
4     0.0      10286.00      2014.0
..    ...           ...         ...
46  199.0      48479.68      2056.0
47  199.0      47109.76      2057.0
48  199.0      45739.84      2058.0
49  199.0      44369.92      2059.0
50  199.0      43000.00      2060.0

[10200 rows x 3 columns]

In [73]:
scenario_10 = new_costs.copy()
scenario_10['gen_fixed_om'] = omc_cost['gen_fixed_om'].values
scenario_10['gen_overnight_cost'] = oc_cost['gen_overnight_cost'].values
scenario_10 = scenario_10[['index','generation_project','build_year','gen_fixed_om','gen_overnight_cost']]
scenario_10

index  generation_project  build_year  gen_fixed_om  gen_overnight_cost
0       0          1300000000        2010      10540.00           346500.00
1       0          1300000000        2011      10476.50           347837.50
2       0          1300000000        2012      10413.00           349175.00
3       0          1300000000        2013      10349.50           350512.50
4       0          1300000000        2014      10286.00           351850.00
..    ...                 ...         ...           ...                 ...
46    199          1300000199        2056      48479.68          1635295.44
47    199          1300000199        2057      47109.76          1591971.58
48    199          1300000199        2058      45739.84          1548647.72
49    199          1300000199        2059      44369.92          1505323.86
50    199          1300000199        2060      43000.00          1462000.00

[10200 rows x 5 columns]

In [74]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_10_gen_build_cost_wave_offshore_wind.csv'
scenario_10.to_csv(output_path,index=False)

In [75]:
path1 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_1_gen_build_cost_wave_offshore_wind.csv'
s1 = pd.read_csv(path1)
s1['scenario_id'] = 1

path2 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_2_gen_build_cost_wave_offshore_wind.csv'
s2 = pd.read_csv(path2)
s2['scenario_id'] = 2

path3 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_3_gen_build_cost_wave_offshore_wind.csv'
s3 = pd.read_csv(path3)
s3['scenario_id'] = 3

path4 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_4_gen_build_cost_wave_offshore_wind.csv'
s4 = pd.read_csv(path4)
s4['scenario_id'] = 4

path5 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_5_gen_build_cost_wave_offshore_wind.csv'
s5 = pd.read_csv(path5)
s5['scenario_id'] = 5

path6 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_6_gen_build_cost_wave_offshore_wind.csv'
s6 = pd.read_csv(path6)
s6['scenario_id'] = 6

path7 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_7_gen_build_cost_wave_offshore_wind.csv'
s7 = pd.read_csv(path7)
s7['scenario_id'] = 7

path8 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_8_gen_build_cost_wave_offshore_wind.csv'
s8 = pd.read_csv(path8)
s8['scenario_id'] = 8

path9 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_9_gen_build_cost_wave_offshore_wind.csv'
s9 = pd.read_csv(path9)
s9['scenario_id'] = 9

path10 = '/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/scenario_10_gen_build_cost_wave_offshore_wind.csv'
s10 = pd.read_csv(path10)
s10['scenario_id'] = 10

In [76]:
s1

index  generation_project  build_year  gen_fixed_om  \
0          0          1300000000        2010    10540.0000   
1          0          1300000000        2011    11351.5000   
2          0          1300000000        2012    12163.0000   
3          0          1300000000        2013    12974.5000   
4          0          1300000000        2014    13786.0000   
...      ...                 ...         ...           ...   
10195    199          1300000199        2056    68247.0049   
10196    199          1300000199        2057    68247.0049   
10197    199          1300000199        2058    68247.0049   
10198    199          1300000199        2059    68247.0049   
10199    199          1300000199        2060    68247.0049   

       gen_overnight_cost  scenario_id  
0                346500.0            1  
1                374387.5            1  
2                402275.0            1  
3                430162.5            1  
4                458050.0            1  
...                   ...          ...  
10195           2185406.8            1  
10196           2185406.8            1  
10197           2185406.8            1  
10198           2185406.8            1  
10199           2185406.8            1  

[10200 rows x 6 columns]

In [77]:
costs_all_scenarios = pd.concat([s1, s2, s3, s4, s5, s6, s7, s8, s9, s10])
costs_all_scenarios

index  generation_project  build_year  gen_fixed_om  \
0          0          1300000000        2010      10540.00   
1          0          1300000000        2011      11351.50   
2          0          1300000000        2012      12163.00   
3          0          1300000000        2013      12974.50   
4          0          1300000000        2014      13786.00   
...      ...                 ...         ...           ...   
10195    199          1300000199        2056      48479.68   
10196    199          1300000199        2057      47109.76   
10197    199          1300000199        2058      45739.84   
10198    199          1300000199        2059      44369.92   
10199    199          1300000199        2060      43000.00   

       gen_overnight_cost  scenario_id  
0               346500.00            1  
1               374387.50            1  
2               402275.00            1  
3               430162.50            1  
4               458050.00            1  
...                   ...          ...  
10195          1635295.44           10  
10196          1591971.58           10  
10197          1548647.72           10  
10198          1505323.86           10  
10199          1462000.00           10  

[102000 rows x 6 columns]

In [78]:
output_path='/Users/nataliagonzalez/Documents/UCSD PhD/2022/Research 2022/Wave Energy/SWITCH Files/scenario_cost_files_v2/all_scenarios_gen_build_cost_wave_offshore_wind.csv'
costs_all_scenarios.to_csv(output_path,index=False)